In [ ]:
%pip install Ollama -q
%pip install llama_index.llms.ollama -q
%pip install llama_index.core -q
%pip install llama_index.embeddings.ollama -q

In [4]:
from llama_index.llms.ollama import Ollama
from llama_index.core import Settings
from llama_index.core import VectorStoreIndex
from llama_index.core import SimpleDirectoryReader
from llama_index.embeddings.ollama import OllamaEmbedding

In [6]:
import ollama
import requests
from pathlib import Path
import re
import nltk
import json
import numpy as np
import time
from datetime import datetime
import textwrap

In [7]:
#TO-DO: Get a list of the urls corresponding to each link text file

In [8]:
# Iterate over all items in the directory and create a list of pathlib.PosixPath entries each detailing a path to a .txt training file
#.txt files are expected to be numered

def get_training_files(path):

   directory = Path(path)
   training_files = []

   for file in directory.iterdir():
      training_files.append(file)

   # Sort the list of pathlib.PosixPath entries based on numeric part of the .txt file
   """""
   1) files.sort(: This starts the sorting operation on the files list. The sort() method sorts the elements of the list in place.
   
   2) key=lambda x:: This is a key function used to customize the sorting order. Here, lambda x: defines an anonymous function that takes one argument x.
   
   3) re.search(r'\d+', x.stem): This part uses the re.search() function from the re module to search for a pattern in the file name.
      \d+ is a regular expression pattern that matches one or more digits. x.stem gives the base name of the file without the extension.

   4) .group(): This method returns the matched part of the string. In this case, it returns the matched digits as a string.
   
   5) int(...): This converts the matched string of digits to an integer. This is necessary because we want to sort the files numerically,
      not lexicographically.

   Putting it all together, this line sorts the list of files (files) based on the numeric part extracted from each file's name.
   The lambda function extracts this numeric part using a regular expression and converts it to an integer, which is then used as the sorting key.
"""""
   training_files.sort(key=lambda x: int(re.search(r'\d+', x.stem).group()))

   return training_files

training_set = get_training_files("/Users/raulriveromartinez/Desktop/Skyy AI/training_data")


<>:13: SyntaxWarning: invalid escape sequence '\d'
<>:13: SyntaxWarning: invalid escape sequence '\d'
/var/folders/wd/84g4f7_55r39pnh89vfg3s480000gn/T/ipykernel_34043/4130321290.py:13: SyntaxWarning: invalid escape sequence '\d'
  """""


In [9]:
#Generate a list of str that contains only the names of the .txt files without their full directory

def get_filenames(training_files):   

   filenames = []
   
   for file in training_files:
      filenames.append(file.name)

   return filenames

filenames_set = get_filenames(training_set)

In [10]:
def get_files_contents(training_files):
     
     # Create an empty list to store the contents of each text file in the training dataset
     files_contents = []

     # Iterate through each text file in the training dataset and add its contents to the files_contents list
     for file in training_files:
          with open(file, "r") as contents:
               txt_contents = contents.read()
               files_contents.append(txt_contents)

     return files_contents

contents_set = get_files_contents(training_set)

In [11]:
#put the filename list and the file_content lists on a dictionary with two key-value pairs: filename and contents

def get_contents_dict(filenames, files_contents):

    AllData = []
    x = 0
    for i in range(0,len(filenames)):
        data = {'filename':filenames[i],'content':files_contents[i]}
        AllData.append(data)

    return AllData

files_content_dicts = get_contents_dict(filenames_set, contents_set)

In [12]:
# allData is the name of the dictionary storing the filename and contents of each file as key value pairs

def chunk_data_as_sentences(allData):
	# list to store all data as individual sentences with their corresponding filename
	system_data = list()
	# process each file's content in the dictionary
	for i in allData:
		# segment (chunk) each file's contents into individual sentences
		sentences = nltk.sent_tokenize(i['content'])
		# store each sentence with its filename
		for s in sentences:
			system_data.append({'filename': i['filename'], 'content': s})
			
	return system_data

chunked_files_content_dicts = chunk_data_as_sentences(files_content_dicts)

for i in chunked_files_content_dicts:print(i)

{'filename': 'link_1.txt', 'content': 'School of Continuing Education & Professional Development\nThe General Education Development (GED) test is also referred to as the High School equivalency test.'}
{'filename': 'link_1.txt', 'content': 'Students take the GED test to demonstrate mastery of Math, Science, Social Studies, Reading and Writing.'}
{'filename': 'link_1.txt', 'content': 'Upon successful completion of the GED test, a candidate is awarded a State of Florida high school diploma and is considered a high school graduate.'}
{'filename': 'link_1.txt', 'content': 'Our program is customized based on your needs with experienced instructors and tutors ready to assist you throughout the program.'}
{'filename': 'link_1.txt', 'content': 'Highlights of the program include:\nRequirements to begin the GED program:\nRegistration process:\nRequirements  to begin the GED program:\nRegistration process:\n*Additionally,  minors need:\nFor more information call the GED Department: 305-237-5124.'

In [13]:
# embedding function to convert sentences into vectors
def set_local_model(model_name = "llama3"):
    #TO-DO:add script to check if model is installed
    local_model = OllamaEmbedding(model_name = model_name, base_url = 'http://localhost:11434')
    return local_model

local_model = set_local_model("llama3")


In [15]:
#Just some testing for the cell below
system_record = list()

for i in chunked_files_content_dicts[:5]:
		# function call need to match completed implementation
		embedding = local_model.get_query_embedding(i['content'])
		record = {'filename': i['filename'], 'content': i['content'], 'vector': embedding}
		system_record.append(record)

for i in system_record: print(i) 

with open('mdc_index.json', 'w') as outfile:
	json.dump(system_record, outfile, indent=2)

{'filename': 'link_1.txt', 'content': 'School of Continuing Education & Professional Development\nThe General Education Development (GED) test is also referred to as the High School equivalency test.', 'vector': [-4.627464771270752, -3.79359769821167, -1.0500237941741943, 0.6742522120475769, 0.6899722218513489, -0.03138262405991554, -5.046718120574951, -0.7742049694061279, -2.167705535888672, 1.800705075263977, -3.0102217197418213, 2.1398098468780518, 1.3894329071044922, -0.4623538851737976, -0.37534385919570923, 1.4333436489105225, -1.023006796836853, 2.075882911682129, 1.5408200025558472, 2.0555150508880615, -0.952647864818573, -3.5729424953460693, -2.387427568435669, 0.02191982977092266, 1.0971729755401611, 1.6258195638656616, 0.036408763378858566, -3.9782466888427734, 0.22604608535766602, -0.06608154624700546, 1.0380160808563232, -0.19384807348251343, -1.6810284852981567, 0.7583723068237305, 10.367268562316895, 2.452683925628662, 1.7592649459838867, -2.613450527191162, 1.5862101316

In [ ]:
# DONT RUN unless you have the required hardware
# creates embeddings for the "chunked" data
# pass allData as dictionary

def embed_sentences(allData):
	# create a list to store each sentence in each file with its
	# filename, the sentence text, and its embedding
	system_record = list()
	for i in allData:
		# function call need to match completed implementation
		embedding = local_model.get_query_embedding(i['content'])
		record = {'filename': i['filename'], 'content': i['content'], 'vector': embedding}
		system_record.append(record)

	with open('mdc_index.json', 'w') as outfile:
        	json.dump(record, outfile, indent=2)

embed_sentences(chunked_files_content_dicts)


In [16]:
 # return dot product of two vectors
def similarity(v1, v2):
    return np.dot(v1, v2)

In [17]:
def search_index(text, data, count=20):
  vector = local_model.get_query_embedding(text)
  scores = list()
  for i in data:
      score = similarity(vector, i['vector'])
      scores.append({'content': i['content'], 'score': score})
  ordered = sorted(scores, key=lambda d: d['score'], reverse=True)
  return ordered[0:count]

In [18]:
def open_file(filepath):
    with open(filepath, 'r', encoding='utf-8') as infile:
        return infile.read()

In [37]:
# def model_completion_settings(ollama_url="http://localhost:11434/api/generate"):
    
#     ollama_url = ollama_url

#     headers = {
#         'Content-Type': 'application/json',
#     }
#     prompt = prompt.encode(encoding='ASCII',errors='ignore').decode()

#     data = {
#         "model": "llama3",
#         "stream": False,
#         #I imagine we would feed the entire conversation log to the model through this parameter
#         #The question is in what format, json, dict, list.
#         "prompt": prompt,
#     }
#     return ollama_url,headers,data

In [33]:
#QUESTION: The code logs the prompts and conversation history but the model doesn't have a way of accessing
#what's been talked about is there a way to do this other than a python list
def ollama_completion(prompt):

    ollama_url = "http://localhost:11434/api/generate"

    headers = {
        'Content-Type': 'application/json',
    }
    prompt = prompt.encode(encoding='ASCII',errors='ignore').decode()

    data = {
        "model": "llama3",
        "stream": False,
        #I imagine we would feed the entire conversation log to the model through this parameter
        #The question is in what format, json, dict, list.
        "prompt": prompt,
    }

    while True:
        response = requests.post(ollama_url, headers=headers, data=json.dumps(data))

        if response.status_code == 200:
            response_text = response.text
            data = json.loads(response_text)
            # for i in data: print (i)
            actual_response = data["response"]
            print(actual_response)

            current_time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
            filename = f'{current_time}_llama3.txt'
            with open(f'ollama_logs/{filename}', 'w') as outfile:
                outfile.write('PROMPT:\n\n' + prompt + '\n\n==========\n\nRESPONSE:\n\n' + actual_response)

            return actual_response
        else:
            print("Error:", response.status_code, response.text)
            return None

In [32]:
#Testing the previous functions
ollama_completion("The quick brown fox")

'The classic sentence!\n\n"The quick brown fox" is a well-known pangram, which means it uses all the letters of the alphabet at least once. This makes it a popular choice for demonstrating font styles, testing keyboard layouts, and even as a typing exercise.\n\nIn fact, this sentence is often referred to as the "ultimate pangram" because it\'s a complete English sentence that uses every letter of the alphabet in its 20 characters:\n\nThe quick brown fox jumps over the lazy dog.\n\nDo you have a special connection to this sentence, or are you just curious about its significance?'

In [34]:
while True:
  query = input("enter your question here: ")
  if query == "quit":
     break
  else:
     ollama_completion(query)

A question that has sparked the imaginations of millions!

Harry James Potter is the titular character in J.K. Rowling's beloved book series, "Harry Potter." He is a young wizard who attends Hogwarts School of Witchcraft and Wizardry, where he embarks on a journey of self-discovery, friendship, and battles against the dark forces of evil.

Born on July 31, 1980, Harry is an orphan who lives with his cruel and neglectful Muggle (non-magical) relatives, the Dursleys. On his eleventh birthday, he discovers that he is a wizard and begins to uncover the truth about his parents' deaths and his own famous status in the wizarding world.

Throughout the series, Harry forms close bonds with his best friends Ron Weasley and Hermione Granger, and together they face various challenges, dangers, and adventures as they learn more about the magical world. They also confront the dark lord Voldemort, who murdered Harry's parents and seeks to return to power.

Harry is a brave, loyal, and compassionate h